In [2]:
!pip install selenium

In [1]:
# 스레드 + 크롤링

from flask import Flask, url_for, request, jsonify, redirect, Response
from flask_cors import CORS, cross_origin

import json
import requests

import selenium
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service

import threading
import time
import logging

import pickle

In [2]:
CRAWLED_RES_SAVED_FILE = 'crawl_data/result'

In [3]:
# 기록용 스레드
def record_thread(cond):
    print("기록용 스레드 구동 시작!")
    cnt = 0
    
    while True:
        if crawl_fin:
            f = open(CRAWLED_RES_SAVED_FILE, 'wb')
            pickle.dump(hrefURL, f)
            f.close()
            
        time.sleep(1)

In [4]:
# 관리 스레드
def thread_manager(cond):
    print("스레드 매니저 구동 시작")
    
    while True:
        with cond:
            if crawl_fin:
                cond.notifyAll()
                
            time.sleep(1)

In [5]:
def crawl_thread(cond, text):
    global crawl_fin
    crawl_fin = False
    
    print("크롤링 스레드 구동 시작!")
    
    url = "https://www.youtube.com/results?search_query="
    
    driver = webdriver.Chrome(r"C:\chromedriver.exe")
    
    search_url = url + text
    
    driver.get(url = search_url)
    
    while True:
        with cond:
            body = driver.find_element_by_tag_name('body')
            
            global hrefURL
            hrefURL = set()
            
            shelfContents = driver.find_elements_by_css_selector(
                "#contents > ytd-shelf-renderer > div > div > ytd-vertical-list-renderer > div > ytd-video-renderer > div > ytd-thumbnail > a"
            )
            
            for item in shelfContents:
                if (item != ''):
                    hrefURL.add(item.get_attribute('href'))
                    
            backup_height = driver.execute_script("return document.body.scrollHeight")
                    
            while True:
                body.send_keys(Keys.END)
                time.sleep(2)
                
                current_height = driver.execute_script("return document.body.scrollHeight")
                
                if backup_height == current_height:
                    break
                    
                backup_height = current_height
                    
            allContents = driver.find_elements_by_css_selector(
                "#contents > ytd-item-section-renderer > div > ytd-video-renderer > div > ytd-thumbnail > a"
            )
            
            for item in allContents:
                if (item != ''):
                    hrefURL.add(item.get_attribute('href'))
            
            print(hrefURL)
            print(len(hrefURL))
            
            crawl_fin = True
            cond.wait()
            crawl_fin = False

In [6]:
if __name__ == '__main__':
    cond = threading.Condition()
    crawler = threading.Thread(name = 'Crawler', target = crawl_thread, args = (cond, '시고르자브종'))
    recorder = threading.Thread(name = 'Recorder', target = record_thread, args = (cond, ))
    manager = threading.Thread(name = 'Manager', target = thread_manager, args = (cond, ))
    
    crawler.start()
    time.sleep(2)
    recorder.start()
    manager.start()

크롤링 스레드 구동 시작!


C:\Users\arim\AppData\Local\Temp\ipykernel_12504\959978392.py:9: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(r"C:\chromedriver.exe")


기록용 스레드 구동 시작!
스레드 매니저 구동 시작


C:\Users\arim\AppData\Local\Temp\ipykernel_12504\959978392.py:17: DeprecationWarning: find_element_by_tag_name is deprecated. Please use find_element(by=By.TAG_NAME, value=name) instead
  body = driver.find_element_by_tag_name('body')
C:\Users\arim\AppData\Local\Temp\ipykernel_12504\959978392.py:22: DeprecationWarning: find_elements_by_css_selector is deprecated. Please use find_elements(by=By.CSS_SELECTOR, value=css_selector) instead
  shelfContents = driver.find_elements_by_css_selector(
C:\Users\arim\AppData\Local\Temp\ipykernel_12504\959978392.py:43: DeprecationWarning: find_elements_by_css_selector is deprecated. Please use find_elements(by=By.CSS_SELECTOR, value=css_selector) instead
  allContents = driver.find_elements_by_css_selector(


{'https://www.youtube.com/watch?v=TLJV0TuJBWw', 'https://www.youtube.com/watch?v=P4Lv_pq0NNY', 'https://www.youtube.com/watch?v=Kz9njANzMQA', 'https://www.youtube.com/watch?v=ADux0rN8G68', 'https://www.youtube.com/watch?v=CPjlGkw9iVE', 'https://www.youtube.com/watch?v=WOKChftHOUA', 'https://www.youtube.com/watch?v=BXQPZD1dgBQ', 'https://www.youtube.com/watch?v=YE5aUwt9mKs', 'https://www.youtube.com/watch?v=PJ5QuJluIWU', 'https://www.youtube.com/watch?v=UUtnh3J8xfQ', 'https://www.youtube.com/watch?v=J1pa4irZwEM', 'https://www.youtube.com/watch?v=mA1sz4nbIV8', 'https://www.youtube.com/shorts/AWsl2aczCFE', 'https://www.youtube.com/watch?v=JLkAv6kwGJw', 'https://www.youtube.com/watch?v=HwIEerKNZqw', 'https://www.youtube.com/watch?v=9KnTJVQRYag', 'https://www.youtube.com/watch?v=42fvJ5skggc', 'https://www.youtube.com/shorts/22_1CRL35Qk', 'https://www.youtube.com/watch?v=_WwtYl1XA1w', 'https://www.youtube.com/watch?v=C689EYbzPuY', 'https://www.youtube.com/watch?v=-lgYmZsFK-U', 'https://www.y

...

{'https://www.youtube.com/watch?v=glYcn1u1Hxc', 'https://www.youtube.com/watch?v=BAFaq4GnokA', 'https://www.youtube.com/shorts/1Fqyse-N5P4', 'https://www.youtube.com/watch?v=g9F3m5fhWmE', 'https://www.youtube.com/shorts/UK69iXd3fE8', 'https://www.youtube.com/watch?v=ZbNrj5ZYQU8', 'https://www.youtube.com/watch?v=gtLUrWBhG_Y', 'https://www.youtube.com/shorts/KWDMkeUF2u8', 'https://www.youtube.com/watch?v=EXITWC1uHmo', 'https://www.youtube.com/shorts/439ksLUS4Ko', 'https://www.youtube.com/watch?v=CPjlGkw9iVE', 'https://www.youtube.com/shorts/Pq1Ucs_ha90', 'https://www.youtube.com/shorts/9bV39BR5Cok', 'https://www.youtube.com/shorts/Rm5g90zpNGU', 'https://www.youtube.com/watch?v=tK-qwKMlbHo', 'https://www.youtube.com/watch?v=KNy0NN8LsBQ', 'https://www.youtube.com/watch?v=nJ4zE05C3Hg', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=yYqYBJoeO8k', 'https://www.youtube.com/watch?v=up64niKxjnE', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube

{'https://www.youtube.com/watch?v=glYcn1u1Hxc', 'https://www.youtube.com/watch?v=BAFaq4GnokA', 'https://www.youtube.com/shorts/1Fqyse-N5P4', 'https://www.youtube.com/watch?v=g9F3m5fhWmE', 'https://www.youtube.com/shorts/UK69iXd3fE8', 'https://www.youtube.com/watch?v=ZbNrj5ZYQU8', 'https://www.youtube.com/watch?v=gtLUrWBhG_Y', 'https://www.youtube.com/shorts/KWDMkeUF2u8', 'https://www.youtube.com/watch?v=EXITWC1uHmo', 'https://www.youtube.com/shorts/439ksLUS4Ko', 'https://www.youtube.com/watch?v=CPjlGkw9iVE', 'https://www.youtube.com/shorts/Pq1Ucs_ha90', 'https://www.youtube.com/shorts/9bV39BR5Cok', 'https://www.youtube.com/shorts/Rm5g90zpNGU', 'https://www.youtube.com/watch?v=tK-qwKMlbHo', 'https://www.youtube.com/watch?v=KNy0NN8LsBQ', 'https://www.youtube.com/watch?v=nJ4zE05C3Hg', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=yYqYBJoeO8k', 'https://www.youtube.com/watch?v=up64niKxjnE', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube

{'https://www.youtube.com/watch?v=glYcn1u1Hxc', 'https://www.youtube.com/watch?v=BAFaq4GnokA', 'https://www.youtube.com/shorts/1Fqyse-N5P4', 'https://www.youtube.com/watch?v=g9F3m5fhWmE', 'https://www.youtube.com/shorts/UK69iXd3fE8', 'https://www.youtube.com/watch?v=ZbNrj5ZYQU8', 'https://www.youtube.com/watch?v=gtLUrWBhG_Y', 'https://www.youtube.com/shorts/KWDMkeUF2u8', 'https://www.youtube.com/watch?v=EXITWC1uHmo', 'https://www.youtube.com/shorts/439ksLUS4Ko', 'https://www.youtube.com/watch?v=CPjlGkw9iVE', 'https://www.youtube.com/shorts/Pq1Ucs_ha90', 'https://www.youtube.com/shorts/9bV39BR5Cok', 'https://www.youtube.com/shorts/Rm5g90zpNGU', 'https://www.youtube.com/watch?v=tK-qwKMlbHo', 'https://www.youtube.com/watch?v=KNy0NN8LsBQ', 'https://www.youtube.com/watch?v=nJ4zE05C3Hg', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=yYqYBJoeO8k', 'https://www.youtube.com/watch?v=up64niKxjnE', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube

{'https://www.youtube.com/watch?v=glYcn1u1Hxc', 'https://www.youtube.com/watch?v=BAFaq4GnokA', 'https://www.youtube.com/shorts/1Fqyse-N5P4', 'https://www.youtube.com/watch?v=g9F3m5fhWmE', 'https://www.youtube.com/shorts/UK69iXd3fE8', 'https://www.youtube.com/watch?v=ZbNrj5ZYQU8', 'https://www.youtube.com/watch?v=gtLUrWBhG_Y', 'https://www.youtube.com/shorts/KWDMkeUF2u8', 'https://www.youtube.com/watch?v=EXITWC1uHmo', 'https://www.youtube.com/shorts/439ksLUS4Ko', 'https://www.youtube.com/watch?v=CPjlGkw9iVE', 'https://www.youtube.com/shorts/Pq1Ucs_ha90', 'https://www.youtube.com/shorts/9bV39BR5Cok', 'https://www.youtube.com/shorts/Rm5g90zpNGU', 'https://www.youtube.com/watch?v=tK-qwKMlbHo', 'https://www.youtube.com/watch?v=KNy0NN8LsBQ', 'https://www.youtube.com/watch?v=nJ4zE05C3Hg', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=yYqYBJoeO8k', 'https://www.youtube.com/watch?v=up64niKxjnE', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube

Exception in thread Crawler:
Traceback (most recent call last):
  File "C:\python\lib\threading.py", line 973, in _bootstrap_inner
    self.run()
  File "C:\python\lib\threading.py", line 910, in run
    self._target(*self._args, **self._kwargs)
  File "C:\Users\arim\AppData\Local\Temp\ipykernel_12504\959978392.py", line 33, in crawl_thread
  File "C:\python\lib\site-packages\selenium\webdriver\remote\webelement.py", line 570, in send_keys
    self._execute(Command.SEND_KEYS_TO_ELEMENT,
  File "C:\python\lib\site-packages\selenium\webdriver\remote\webelement.py", line 740, in _execute
    return self._parent.execute(command, params)
  File "C:\python\lib\site-packages\selenium\webdriver\remote\webdriver.py", line 430, in execute
    self.error_handler.check_response(response)
  File "C:\python\lib\site-packages\selenium\webdriver\remote\errorhandler.py", line 247, in check_response
    raise exception_class(message, screen, stacktrace)
selenium.common.exceptions.WebDriverException: Mes

In [7]:
import pickle

f = open(CRAWLED_RES_SAVED_FILE, 'rb')
hrefURL = pickle.load(f)
f.close()

print(hrefURL)
print(len(hrefURL))

{'https://www.youtube.com/watch?v=mnAqq24C_Uw', 'https://www.youtube.com/watch?v=-lgYmZsFK-U', 'https://www.youtube.com/watch?v=cuCNR-nJ1Qc', 'https://www.youtube.com/watch?v=zKr8gmdoZlg', 'https://www.youtube.com/watch?v=WCwzgU_waiA', 'https://www.youtube.com/watch?v=dQO6zvdyvKk', 'https://www.youtube.com/watch?v=mLKJyAN4Hww', 'https://www.youtube.com/watch?v=Zn9cmb3RqsE', 'https://www.youtube.com/watch?v=hb2j1v5urpk', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.youtube.com/watch?v=QmUHJcd13fg', 'https://www.youtube.com/watch?v=Q3yLvk4kDwE', 'https://www.youtube.com/shorts/bYRtX-nc4dM', 'https://www.youtube.com/watch?v=7QzPXT-LDOY', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/shorts/ntDENg1BhHQ', 'https://www.youtube.com/watch?v=5ed6yr5Nqbs', 'https://www.youtube.com/watch?v=93vTNpqT0-k', 'https://www.youtube.com/shorts/7EtbidAwB_c', 'https://www.youtube.com/shorts/0Sz8oURtdh0', 'https://www.yout

{'https://www.youtube.com/watch?v=mnAqq24C_Uw', 'https://www.youtube.com/watch?v=-lgYmZsFK-U', 'https://www.youtube.com/watch?v=cuCNR-nJ1Qc', 'https://www.youtube.com/watch?v=zKr8gmdoZlg', 'https://www.youtube.com/watch?v=WCwzgU_waiA', 'https://www.youtube.com/watch?v=dQO6zvdyvKk', 'https://www.youtube.com/watch?v=mLKJyAN4Hww', 'https://www.youtube.com/watch?v=Zn9cmb3RqsE', 'https://www.youtube.com/watch?v=hb2j1v5urpk', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.youtube.com/watch?v=QmUHJcd13fg', 'https://www.youtube.com/watch?v=Q3yLvk4kDwE', 'https://www.youtube.com/shorts/bYRtX-nc4dM', 'https://www.youtube.com/watch?v=7QzPXT-LDOY', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/shorts/ntDENg1BhHQ', 'https://www.youtube.com/watch?v=5ed6yr5Nqbs', 'https://www.youtube.com/watch?v=93vTNpqT0-k', 'https://www.youtube.com/shorts/7EtbidAwB_c', 'https://www.youtube.com/shorts/0Sz8oURtdh0', 'https://www.yout

C:\Users\arim\AppData\Local\Temp\ipykernel_7904\959978392.py:17: DeprecationWarning: find_element_by_tag_name is deprecated. Please use find_element(by=By.TAG_NAME, value=name) instead
  body = driver.find_element_by_tag_name('body')
C:\Users\arim\AppData\Local\Temp\ipykernel_7904\959978392.py:22: DeprecationWarning: find_elements_by_css_selector is deprecated. Please use find_elements(by=By.CSS_SELECTOR, value=css_selector) instead
  shelfContents = driver.find_elements_by_css_selector(
C:\Users\arim\AppData\Local\Temp\ipykernel_7904\959978392.py:43: DeprecationWarning: find_elements_by_css_selector is deprecated. Please use find_elements(by=By.CSS_SELECTOR, value=css_selector) instead
  allContents = driver.find_elements_by_css_selector(


{'https://www.youtube.com/watch?v=mnAqq24C_Uw', 'https://www.youtube.com/watch?v=-lgYmZsFK-U', 'https://www.youtube.com/watch?v=cuCNR-nJ1Qc', 'https://www.youtube.com/watch?v=zKr8gmdoZlg', 'https://www.youtube.com/watch?v=WCwzgU_waiA', 'https://www.youtube.com/watch?v=dQO6zvdyvKk', 'https://www.youtube.com/watch?v=mLKJyAN4Hww', 'https://www.youtube.com/watch?v=Zn9cmb3RqsE', 'https://www.youtube.com/watch?v=hb2j1v5urpk', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.youtube.com/watch?v=QmUHJcd13fg', 'https://www.youtube.com/watch?v=Q3yLvk4kDwE', 'https://www.youtube.com/shorts/bYRtX-nc4dM', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=7QzPXT-LDOY', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube.com/shorts/ntDENg1BhHQ', 'https://www.youtube.com/watch?v=5ed6yr5Nqbs', 'https://www.youtube.com/watch?v=93vTNpqT0-k', 'https://www.youtube.com/shorts/7EtbidAwB_c', 'https://www.youtube.com/shorts/0Sz8oURtdh0', 'https://www.yout

{'https://www.youtube.com/watch?v=mnAqq24C_Uw', 'https://www.youtube.com/watch?v=-lgYmZsFK-U', 'https://www.youtube.com/watch?v=cuCNR-nJ1Qc', 'https://www.youtube.com/watch?v=zKr8gmdoZlg', 'https://www.youtube.com/watch?v=WCwzgU_waiA', 'https://www.youtube.com/watch?v=dQO6zvdyvKk', 'https://www.youtube.com/watch?v=mLKJyAN4Hww', 'https://www.youtube.com/watch?v=Zn9cmb3RqsE', 'https://www.youtube.com/watch?v=hb2j1v5urpk', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.youtube.com/watch?v=QmUHJcd13fg', 'https://www.youtube.com/watch?v=Q3yLvk4kDwE', 'https://www.youtube.com/shorts/bYRtX-nc4dM', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=7QzPXT-LDOY', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube.com/shorts/ntDENg1BhHQ', 'https://www.youtube.com/watch?v=5ed6yr5Nqbs', 'https://www.youtube.com/watch?v=93vTNpqT0-k', 'https://www.youtube.com/shorts/7EtbidAwB_c', 'https://www.youtube.com/shorts/0Sz8oURtdh0', 'https://www.yout

{'https://www.youtube.com/watch?v=mnAqq24C_Uw', 'https://www.youtube.com/watch?v=-lgYmZsFK-U', 'https://www.youtube.com/watch?v=cuCNR-nJ1Qc', 'https://www.youtube.com/watch?v=zKr8gmdoZlg', 'https://www.youtube.com/watch?v=WCwzgU_waiA', 'https://www.youtube.com/watch?v=dQO6zvdyvKk', 'https://www.youtube.com/watch?v=mLKJyAN4Hww', 'https://www.youtube.com/watch?v=Zn9cmb3RqsE', 'https://www.youtube.com/watch?v=hb2j1v5urpk', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.youtube.com/watch?v=QmUHJcd13fg', 'https://www.youtube.com/watch?v=Q3yLvk4kDwE', 'https://www.youtube.com/shorts/bYRtX-nc4dM', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=7QzPXT-LDOY', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube.com/shorts/ntDENg1BhHQ', 'https://www.youtube.com/watch?v=5ed6yr5Nqbs', 'https://www.youtube.com/watch?v=93vTNpqT0-k', 'https://www.youtube.com/shorts/7EtbidAwB_c', 'https://www.youtube.com/shorts/0Sz8oURtdh0', 'https://www.yout

{'https://www.youtube.com/watch?v=mnAqq24C_Uw', 'https://www.youtube.com/watch?v=-lgYmZsFK-U', 'https://www.youtube.com/watch?v=cuCNR-nJ1Qc', 'https://www.youtube.com/watch?v=zKr8gmdoZlg', 'https://www.youtube.com/watch?v=WCwzgU_waiA', 'https://www.youtube.com/watch?v=dQO6zvdyvKk', 'https://www.youtube.com/watch?v=mLKJyAN4Hww', 'https://www.youtube.com/watch?v=Zn9cmb3RqsE', 'https://www.youtube.com/watch?v=hb2j1v5urpk', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.youtube.com/watch?v=QmUHJcd13fg', 'https://www.youtube.com/watch?v=Q3yLvk4kDwE', 'https://www.youtube.com/shorts/bYRtX-nc4dM', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=7QzPXT-LDOY', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube.com/shorts/ntDENg1BhHQ', 'https://www.youtube.com/watch?v=5ed6yr5Nqbs', 'https://www.youtube.com/watch?v=93vTNpqT0-k', 'https://www.youtube.com/shorts/7EtbidAwB_c', 'https://www.youtube.com/shorts/0Sz8oURtdh0', 'https://www.yout

{'https://www.youtube.com/watch?v=mnAqq24C_Uw', 'https://www.youtube.com/watch?v=-lgYmZsFK-U', 'https://www.youtube.com/watch?v=cuCNR-nJ1Qc', 'https://www.youtube.com/watch?v=zKr8gmdoZlg', 'https://www.youtube.com/watch?v=WCwzgU_waiA', 'https://www.youtube.com/watch?v=dQO6zvdyvKk', 'https://www.youtube.com/watch?v=mLKJyAN4Hww', 'https://www.youtube.com/watch?v=Zn9cmb3RqsE', 'https://www.youtube.com/watch?v=hb2j1v5urpk', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.youtube.com/watch?v=QmUHJcd13fg', 'https://www.youtube.com/watch?v=Q3yLvk4kDwE', 'https://www.youtube.com/shorts/bYRtX-nc4dM', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=7QzPXT-LDOY', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube.com/shorts/ntDENg1BhHQ', 'https://www.youtube.com/watch?v=5ed6yr5Nqbs', 'https://www.youtube.com/watch?v=93vTNpqT0-k', 'https://www.youtube.com/shorts/7EtbidAwB_c', 'https://www.youtube.com/shorts/0Sz8oURtdh0', 'https://www.yout

{'https://www.youtube.com/watch?v=mnAqq24C_Uw', 'https://www.youtube.com/watch?v=-lgYmZsFK-U', 'https://www.youtube.com/watch?v=cuCNR-nJ1Qc', 'https://www.youtube.com/watch?v=zKr8gmdoZlg', 'https://www.youtube.com/watch?v=WCwzgU_waiA', 'https://www.youtube.com/watch?v=dQO6zvdyvKk', 'https://www.youtube.com/watch?v=mLKJyAN4Hww', 'https://www.youtube.com/watch?v=Zn9cmb3RqsE', 'https://www.youtube.com/watch?v=hb2j1v5urpk', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.youtube.com/watch?v=QmUHJcd13fg', 'https://www.youtube.com/watch?v=Q3yLvk4kDwE', 'https://www.youtube.com/shorts/bYRtX-nc4dM', 'https://www.youtube.com/watch?v=gGPVIkSZ8lA', 'https://www.youtube.com/watch?v=7QzPXT-LDOY', 'https://www.youtube.com/shorts/q-biGHZjjYo', 'https://www.youtube.com/shorts/ntDENg1BhHQ', 'https://www.youtube.com/watch?v=5ed6yr5Nqbs', 'https://www.youtube.com/watch?v=93vTNpqT0-k', 'https://www.youtube.com/shorts/7EtbidAwB_c', 'https://www.youtube.com/shorts/0Sz8oURtdh0', 'https://www.yout

In [ ]:
# 스레드 사용없이 

url = "https://www.youtube.com/results?search_query="

driver = webdriver.Chrome(r"C:\chromedriver.exe")
cnt = 0

search_url = url + "시고르자브종"
driver.get(url = search_url)

body = driver.find_element_by_tag_name('body')

hrefURL = set()

shelfContents = driver.find_elements_by_css_selector(
    "#contents > ytd-shelf-renderer > div > div > ytd-vertical-list-renderer > div > ytd-video-renderer > div > ytd-thumbnail > a"
)

for item in shelfContents:
    if (item != ''):
        hrefURL.add(item.get_attribute('href'))

backup_height = driver.execute_script("return document.body.scrollHeight")

while cnt < 1000:
    body.send_keys(Keys.END)
    cnt += 1

allContents = driver.find_elements_by_css_selector(
    "#contents > ytd-item-section-renderer > div > ytd-video-renderer > div > ytd-thumbnail > a"
)

for item in allContents:
    if (item != ''):
        hrefURL.add(item.get_attribute('href'))

print(hrefURL)
print(len(hrefURL))